In [1]:
from os import remove
# Implementacja dwu-warstwowego modelu klimat dla aqua-planety
# Python w nakładce COLAB (sprawdzić Jupiter)
# Krzysztof Markowicz, kmark@igf.fuw.edu.pl
# Aktualizacja 19Oct2025

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from ipywidgets import interact, Dropdown
from scipy.optimize import minimize

# --- Parametry modelu ---
Lambda = 0.67              # Climate sensitivity K/W/m2
Y=1/Lambda                 # Parametr sprzężenia zwrotnego
dens=1000                  # gęstość wody kg/m3
Cp=4218                    # ciepło właściwe dla wody
H_mixed = 100              # grubość warstwy mieszania [m]
H_deep  = 3900             # grubość warstwy głębinowej [m]
C_mixed = dens*Cp*H_mixed  # Pojemność cieplna [J/kg] dla warstwy mieszania
C_deep  = dens*Cp*H_deep   # Pojemność cieplna [J/kg] dla warstwy głębinowej
diffusivity = 0.0001       # Współczynik dyfuzji turbulencyjnej [m²/s] wymiana ciepła pomiędzy warstwami modelu
dt = 3600*24*365           # krok czasowy w [s]
scale =1                   # Parametr do skalowania wymuszania radiacyjnego
# ----Wczytanie danych obejmujących wymuszanie radiacyjne ---
from google.colab import drive
drive.mount('/content/drive')
plik = "/content/drive/MyDrive/PracowniaGGG/AR6_ERF_1750-2019.csv"
plikIPCC = "/content/drive/MyDrive/PracowniaGGG/ScenariuszeIPCC.xlsx"
RF = pd.read_csv(plik)
# --- 🔍 Sprawdź strukturę danych ---
print("Kolumny w pliku:")
print(RF.columns.tolist())
# --- 📅 Wybierz lata i podstawowe składniki ---
kolumny = ['year', 'co2', 'ch4', 'n2o', 'other_wmghg', 'o3', 'h2o_stratospheric', 'contrails', 'aerosol-radiation_interactions', 'aerosol-cloud_interactions', 'bc_on_snow', 'land_use', 'volcanic', 'solar', 'nonco2_wmghg', 'aerosol', 'chapter2_other_anthro', 'total_anthropogenic', 'total_natural', 'total']
RF = RF[kolumny]
# --- 🧹 Ogranicz do interesującego zakresu (np. 1850–2019) ---
RF = RF[(RF['year'] >= 1850) & (RF['year'] <= 2019)]

# ----  Dodatnie nowej kolumny dla systetycznych wymuszen radiacyjnych (np. wulkanicznych)
RF['volcanic_add']=0
# --- Parametry erupcji ---
eruption_year = 1982          # Rok erupcji wulkanu
eruption_strength = -2.0      # Maksymalne wymuszenie [W/m2]
tau = 5                       # Stała zaniku (lata)
def volcanic_forcing(year):
    if year < eruption_year:
        return 0
    t = year - eruption_year
    return eruption_strength * np.exp(-t / tau)

RF["volcanic_add"] = RF["year"].apply(volcanic_forcing)

# ---- Dodatnie scenariujsza usuniecia wszystkich gazów cieplarnianych poza parą wodną
RF['GHG_remove']=0
remove_year = 1950          # Rok erupcji wulkanu
remove_strength = -40.0      # Maksymalne wymuszenie [W/m2]
tau = 25                       # Stała zaniku (lata)
def GHGremove_forcing(year):
    if year < remove_year:
        return 0
    t = year - remove_year
    return remove_strength

RF["GHG_remove"] = RF["year"].apply(GHGremove_forcing)

# ----Wczytanie anomalii temperatury ---
plik = "/content/drive/MyDrive/PracowniaGGG/HadCRUT.5.1.0.0.analysis.summary_series.global.annual.csv"
Temp = pd.read_csv(plik)
# --- 🧹 Ogranicz do interesującego zakresu (np. 1850–2019) ---
print(Temp.columns.tolist())
Temp = Temp[(Temp['Time'] >= 1750) & (Temp['Time'] <= 2019)]
# Korekcja anomalii temperatury do pierwszych 30 lat
dT=Temp['Anomaly (deg C)']
dT=dT-np.mean(dT[:30])
dT_ave = pd.Series(dT).rolling(window=5, center=False).mean()

# ------- Scenariusze SSP--------------------------------------
sheets = pd.read_excel(plikIPCC, sheet_name=None)  # None = wszystkie arkusze
print(sheets.keys())  # nazwy arkuszy
#Dostęp do konkretnej zakładki: 'SSP1_19', 'SSP1_26', 'SSP1_45', 'SSP_70', 'SSP1_85'
SSP19=sheets["SSP1_19"]
SSP26=sheets["SSP1_26"]
SSP45=sheets["SSP1_45"]
SSP70=sheets["SSP1_70"]
SSP85=sheets["SSP1_85"]

SSP19=SSP19[(SSP19['Year'] >= 2000) & (SSP19['Year'] <= 2100)]
SSP26=SSP26[(SSP19['Year'] >= 2000) & (SSP26['Year'] <= 2100)]
SSP45=SSP45[(SSP19['Year'] >= 2000) & (SSP45['Year'] <= 2100)]
SSP70=SSP70[(SSP19['Year'] >= 2000) & (SSP70['Year'] <= 2100)]
SSP85=SSP85[(SSP19['Year'] >= 2000) & (SSP85['Year'] <= 2100)]
print(SSP19.columns.tolist())

def interpolate_annual(df):
    # Upewniamy się, że Year jest typu int
    df['Year'] = df['Year'].astype(int)
    # Ustawiamy Year jako indeks
    df = df.set_index('Year')
    # Dodajemy brakujące lata
    df = df.reindex(range(df.index.min(), df.index.max() + 1))
    # Interpolacja liniowa
    df = df.interpolate(method='linear')
    # Przywracamy Year jako kolumnę
    df = df.reset_index()
    return df

SSP19=interpolate_annual(SSP19)
SSP26=interpolate_annual(SSP26)
SSP45=interpolate_annual(SSP45)
SSP70=interpolate_annual(SSP70)
SSP85=interpolate_annual(SSP85)

# --- Model klimatu zapisany w funkcji---
def model(RFtype,Lambda):
  T_mixed = np.zeros(len(RF))
  T_deep  = np.zeros(len(RF))
  Teq= np.zeros(len(RF))
  for i in range(1, len(RF)):
    F = scale*RF[RFtype].iloc[i]  # W/m²
    Flux=diffusivity*dens*Cp*1/2*(T_mixed[i-1]-T_deep[i-1])/(H_mixed+H_deep)
    T_deep[i]=T_deep[i-1]+dt/C_deep*Flux
    T_mixed[i]=T_mixed[i-1]+dt/C_mixed*(F-Flux-T_mixed[i-1]/Lambda)
    Teq[i] = F*Lambda
  return T_mixed, T_deep, Teq

# Funkcja do minimalizacji roznicy pomiedzy modelem a obserwacjami
def funmin(Lambda):
    T_pred,Ta,Tb = model('total', Lambda)
    return np.sum((T_pred - dT)**2)

result = minimize(funmin, x0=[0.67])  #
print("Climate Sensitivity",result)
# ---- Start modelu ---
#T_mixed, T_deep, Teq = model('total')

forcing = RF.columns.tolist()[1:]
@interact(component = Dropdown(options=forcing, description='Radiative Forcing:'))
def plot_forcing(component):
  T_mixed, T_deep, Teq = model(component,Lambda)
  # --- Wykres wyników ---
  plt.figure(figsize=(12,5))
  plt.plot(RF['year'], T_mixed, label='Temperatura warstwy mieszania')
  plt.plot(RF['year'], T_deep, label='Temperatura warstwy głębinowej')
  plt.plot(Temp['Time'], dT, label='Temperatura na podstawie pomiarów',color='green', linestyle='--',)
  plt.plot(Temp['Time'], dT_ave, label='Temperatura na podstawie - średnia ruchoma pomiarów',color='green')
  plt.plot(RF['year'],Teq,label='Temperatura równowagowa warstwy mieszania')
  plt.xlabel('Rok')
  plt.ylabel('Anomalia temperatury [K]')
  plt.title('2-warstwowy model klimatu (aqua-planeta)')
  plt.legend()
  plt.grid(True)
  plt.show()
  # --- Liczenie BIAS, RMSE współ, korelacji Pearsona ---
  bias = round(np.mean(T_mixed - dT),2)
  rmse = round(np.sqrt(np.mean((T_mixed - dT)**2)),2)
  corr = np.corrcoef(T_mixed,dT)[0,1]
  print("Statystyka zgodności modelu od 1850 r.:")
  print("BIAS=",bias," K")
  print("RMSE=",rmse," K")
  print("Corr=",round(corr,2))

  print("Statystyka zgodności modelu dla ostatnich 30 lat")
  bias = round(np.mean(T_mixed[-30:] - dT[-30:]),2)
  rmse = round(np.sqrt(np.mean((T_mixed[-30:] - dT[-30:])**2)),2)
  corr = np.corrcoef(T_mixed[-30:],dT[-30:])[0,1]
  print("BIAS=",bias," K")
  print("RMSE=",rmse," K")
  print("Corr=",round(corr,2))

  bias = round(np.mean(Teq-dT),2)
  rmse = round(np.sqrt(np.mean((dT-Teq)**2)),2)
  corr = np.corrcoef(Teq, dT)[0, 1]
  print("Statystyka temperatury równowagowej od 19850 r.:")
  print("BIAS=",bias," K")
  print("RMSE=",rmse," K")
  print("Corr=",round(corr,2))



Mounted at /content/drive
Kolumny w pliku:
['year', 'co2', 'ch4', 'n2o', 'other_wmghg', 'o3', 'h2o_stratospheric', 'contrails', 'aerosol-radiation_interactions', 'aerosol-cloud_interactions', 'bc_on_snow', 'land_use', 'volcanic', 'solar', 'nonco2_wmghg', 'aerosol', 'chapter2_other_anthro', 'total_anthropogenic', 'total_natural', 'total']
['Time', 'Anomaly (deg C)', 'Lower confidence limit (2.5%)', 'Upper confidence limit (97.5%)']
dict_keys(['SSP1_19', 'SSP1_26', 'SSP1_45', 'SSP1_70', 'SSP1_85'])
['Year', 'CO2', 'CH4', 'N2O', 'Halogens', 'O3', 'H2O STRAT 2', 'Contrail-cirrus', 'Aerosol radiation interactions', 'Aerosol cloud interactions', 'BC on snow', 'Land use', 'Volcanic', 'Solar', 'Total anthropogenic', 'Total natural', 'Total']
Climate Sensitivity   message: Optimization terminated successfully.
  success: True
   status: 0
      fun: 3.498869480183082
        x: [ 5.270e-01]
      nit: 4
      jac: [-2.086e-07]
 hess_inv: [[ 8.203e-03]]
     nfev: 17
     njev: 7


/tmp/ipython-input-277770407.py:97: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Year'].astype(int)
/tmp/ipython-input-277770407.py:97: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Year'] = df['Year'].astype(int)
/tmp/ipython-input-277770407.py:97: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

interactive(children=(Dropdown(description='Radiative Forcing:', options=('co2', 'ch4', 'n2o', 'other_wmghg', …